### rendering directly via mujoco (no mjx)

In [13]:
import mediapy as media
from dm_control import mjcf
from dm_control.mujoco.wrapper.mjbindings import enums
import mujoco
from jax import numpy as jnp
import pickle
import imageio
import numpy as np
import os
%cd stac-mjx
import controller
import utils
import stac_base

os.environ["MUJOCO_GL"] = "osmesa"
offset_path = "../standard_fit_6loops.p"

scene_option = mujoco.MjvOption()
# scene_option.geomgroup[1] = 0
scene_option.geomgroup[2] = 1
# scene_option.geomgroup[3] = 0
# scene_option.sitegroup[0] = 0
# scene_option.sitegroup[1] = 0
scene_option.sitegroup[2] = 1

scene_option.sitegroup[3] = 1
scene_option.flags[enums.mjtVisFlag.mjVIS_TRANSPARENT] = True
scene_option.flags[enums.mjtVisFlag.mjVIS_LIGHT] = False
scene_option.flags[enums.mjtVisFlag.mjVIS_CONVEXHULL] = True
scene_option.flags[enums.mjtRndFlag.mjRND_SHADOW] = False
scene_option.flags[enums.mjtRndFlag.mjRND_REFLECTION] = False
scene_option.flags[enums.mjtRndFlag.mjRND_SKYBOX] = False
scene_option.flags[enums.mjtRndFlag.mjRND_FOG] = False

[Errno 2] No such file or directory: 'stac-mjx'
/Users/charleszhang/GitHub/stac-mjx/stac-mjx


In [14]:
utils.init_params("../params/params.yaml")

# load mjx_model and mjx_data and set marker sites
rat_xml = "../models/rodent_stac.xml"
root = mjcf.from_path(rat_xml)
physics, mj_model = controller.create_body_sites(root)
physics, mj_model, keypoint_sites = controller.create_keypoint_sites(root)

#starting xpos anda xquat for mjdata
_UPRIGHT_POS = (0.0, 0.0, 0.94)
_UPRIGHT_QUAT = (0.859, 1.0, 1.0, 0.859)

In [15]:
# mjx_data = stac_base.kinematics(mjx_model, mjx_data)
mj_data = mujoco.MjData(mj_model)
mj_data.xpos = _UPRIGHT_POS
mj_data.xquat = _UPRIGHT_QUAT
mujoco.mj_kinematics(mj_model, mj_data)

### Full video rendering directly using mujoco

In [17]:
# open data file, loop through qpos blah blah
# offset_path="../LM_fit.p"
with open(offset_path, "rb") as file:
    d = pickle.load(file)
    qposes = np.array(d["qpos"])
    kp_data = np.array(d["kp_data"])


FPS=50
n_frames = 2000
frames=[]
save_path="../videos/direct_render.mp4"
renderer = mujoco.Renderer(mj_model, height=1200, width=1920)
# Make sure there are enough frames to render
if qposes.shape[0] < n_frames-1:
    raise Exception(f"Trying to render {n_frames} frames when data['qpos'] only has {qposes.shape[0]}")

# slice kp_data to match qposes length
kp_data = kp_data[:qposes.shape[0]]

# render while stepping using mujoco, not mjx
with imageio.get_writer(save_path, fps=FPS) as video:
    for i, (qpos, kps) in enumerate(zip(qposes, kp_data)):
        if i%100 == 0:
            print(f"rendering frame {i}")
        if i == n_frames:
            break
        
        #set keypoints
        physics, mj_model = controller.set_keypoint_sites(physics, keypoint_sites, kps)
        mj_data.qpos = qpos
        mujoco.mj_forward(mj_model, mj_data)

        renderer.update_scene(mj_data, camera="close_profile", scene_option=scene_option)
        pixels = renderer.render()
        video.append_data(pixels)
        frames.append(pixels)

media.show_video(frames, fps=FPS)

rendering frame 0
rendering frame 100
rendering frame 200
rendering frame 300
rendering frame 400
rendering frame 500
rendering frame 600
rendering frame 700
rendering frame 800
rendering frame 900
rendering frame 1000
rendering frame 1100
rendering frame 1200
rendering frame 1300
rendering frame 1400
rendering frame 1500
rendering frame 1600
rendering frame 1700
rendering frame 1800
rendering frame 1900


This browser does not support the video tag.


### Testing new viz.py (should do same as above)

In [1]:
%cd stac-mjx
import mediapy as media
import os
from viz import mujoco_viz
import utils


os.environ["MUJOCO_GL"] = "osmesa"

# set args and initialize params
rat_xml = "../models/rodent_stac.xml"
data_path = "../standard_fit_6loops.p"
params_path = "../params/params.yaml"
n_frames=2000
save_path="../videos/direct_render.mp4"
utils.init_params(params_path)

# call viz and show video
frames = mujoco_viz(data_path, rat_xml, n_frames, save_path)
media.show_video(frames, fps=utils.params["RENDER_FPS"])

/Users/charleszhang/GitHub/stac-mjx/stac-mjx


/Users/charleszhang/miniforge3/envs/stac-mjx/lib/python3.12/site-packages/imageio_ffmpeg/_utils.py:7: DeprecationWarning: pkg_resources is deprecated as an API. See https://setuptools.pypa.io/en/latest/pkg_resources.html
  from pkg_resources import resource_filename


rendering frame 0
rendering frame 100
rendering frame 200
rendering frame 300
rendering frame 400
rendering frame 500
rendering frame 600
rendering frame 700
rendering frame 800
rendering frame 900
rendering frame 1000
rendering frame 1100
rendering frame 1200
rendering frame 1300
rendering frame 1400
rendering frame 1500
rendering frame 1600
rendering frame 1700
rendering frame 1800
rendering frame 1900


This browser does not support the video tag.
